In [1]:
from sklearn.decomposition import TruncatedSVD
import gensim
from pymorphy2 import MorphAnalyzer
import pymorphy2
from tqdm.auto import tqdm
import numpy as np
import plotly.express as px

In [30]:
def get_matrix(all_nouns):
    all2 = [word for word in all_nouns if word in model.wv.index_to_key]
    vectors_of_words = np.zeros((len(all2), model.vector_size))
    model_wordlist =  model.wv.index_to_key
    for i, word in enumerate(all2):
            vectors_of_words[i] = model.wv[word]
        
    return vectors_of_words

def lsa_matrix(vectors_of_words, n_components, n_iter=100):
    lsa_obj = TruncatedSVD(n_components=n_components, n_iter=n_iter, random_state=42)
    lsa_data = lsa_obj.fit_transform(vectors_of_words)
    return lsa_data


In [7]:
model_file = './all_cyberleninka_20_epochs/all_cyberleninka_20epoches.model'
model = gensim.models.Word2Vec.load(model_file)

In [8]:
morpho = MorphAnalyzer()

In [36]:
with open('very_clean_list.txt', encoding='utf8') as f:
    all_nouns = f.read().split('\n')

In [37]:
def is_predicted(word):
    parse_result = morpho.parse(word)[0]
    for r in parse_result.methods_stack:
        if type(r[0]) in [pymorphy2.units.by_analogy.UnknownPrefixAnalyzer, 
                          pymorphy2.units.by_analogy.KnownSuffixAnalyzer]:
            return True
        
    return False

In [38]:
all_nouns2 = []
for noun in tqdm(all_nouns[:-1]):
    res = morpho.parse(noun)
    if not is_predicted(noun):
        all_nouns2.append(noun)


  0%|          | 0/32467 [00:00<?, ?it/s]

In [39]:
all_nouns = all_nouns2

In [45]:
len(all_nouns)

24847

In [46]:
%%time
first_matrix = get_matrix(all_nouns)
print(1)
first_lsa = lsa_matrix(first_matrix, 3)

1
Wall time: 13.3 s


In [108]:
import os
import pandas as pd
import random

#one_word_dicts
dict_dir = './dicts/words'
#то, что собрано руками
dict_add_dir = './dicts/add_words'

def get_dicts(dict_dir, dict_add_dir):
    all_data = {}

    for file in os.listdir(dict_dir):
        if file.endswith('one_word_terms.txt'):

            wordlist = []

            with open(os.path.join(dict_dir, file), encoding='utf8') as f:
                wordlist.extend(f.read().split())

            name = file.split('_')[0]

            all_data[name] = [i for i in wordlist if i in all_nouns]

    for file in os.listdir(dict_add_dir):
        wordlist = []

        with open(os.path.join(dict_add_dir, file), encoding='utf8') as f:
            wordlist.extend(f.read().split())

        name = file.split('.')[0]

        all_data[name] = [i for i in wordlist if i in all_nouns] 
        
    return all_data

def get_colors():
    colors_table = pd.read_csv('colors.txt', names=['tag', 'name', 'html', 'r', 'g', 'b'])

    all_colors = {}

    for key in all_data.keys():
        i = random.randint(0, 865)
        all_colors[key] = f'rgb({colors_table.r[i]},{colors_table.g[i]},{colors_table.b[i]})'
    return all_colors

In [96]:
all_colors

{'anatomy': 'rgb(255,127,80)',
 'botanics': 'rgb(223,115,255)',
 'byology': 'rgb(233,116,81)',
 'chemistry': 'rgb(121,104,120)',
 'economics': 'rgb(0,49,83)',
 'finance': 'rgb(0,75,73)',
 'geology': 'rgb(191,79,81)',
 'hystory': 'rgb(217,144,88)',
 'law': 'rgb(221,173,175)',
 'linguistics': 'rgb(145,92,131)',
 'mathematics': 'rgb(227,0,34)',
 'medicine': 'rgb(0,51,153)',
 'military': 'rgb(112,66,65)',
 'physics': 'rgb(226,88,34)',
 'plants': 'rgb(255,160,122)',
 'religion': 'rgb(147,112,219)',
 'sport': 'rgb(255,167,0)',
 'technics': 'rgb(13,152,186)',
 'zoology': 'rgb(250,218,94)',
 'architecture': 'rgb(204,78,92)',
 'informatics': 'rgb(147,204,234)',
 'names': 'rgb(250,214,165)',
 'philology': 'rgb(0,255,0)',
 'philosophy': 'rgb(171,205,239)'}

In [110]:
all_data.keys()

dict_keys(['anatomy', 'botanics', 'byology', 'chemistry', 'economics', 'finance', 'geology', 'hystory', 'law', 'linguistics', 'mathematics', 'medicine', 'military', 'physics', 'plants', 'religion', 'sport', 'technics', 'zoology', 'architecture', 'informatics', 'names', 'philology', 'philosophy'])

In [160]:
from ipywidgets import FloatRangeSlider

slider = FloatRangeSlider(min=-100, max=100, step=0.1)

In [161]:
slider

FloatRangeSlider(value=(-50.0, 50.0), min=-100.0)

In [146]:
slider.value

(12.2, 20.0)

In [155]:
def get_graph_3d(first_lsa, all_nouns=all_nouns, all_data=all_data, all_colors=all_colors):
    s = [1 for a in first_lsa]
    c = ['rgb(254,255,255)' for a in first_lsa]

    for i, noun in enumerate(all_nouns):
        for key, value in all_data.items():
            if noun in value:
                c[i] = all_colors[key]
                
    first_slider = (slider.value[0] < first_lsa[:,0]) & (slider.value[1] > first_lsa[:,0])# < slider.value[1]]    

    second_lsa = first_lsa[first_slider]
    
    
    
    fig = px.scatter_3d(x=second_lsa[:,0], y=second_lsa[:,1], z=second_lsa[:,2],
                        size=np.array(s)[first_slider], 
                        size_max=2, opacity=0.7, 
                        hover_name=np.array(all_nouns)[first_slider])


    fig.update_traces(marker=dict(size=2,
                                  line=dict(width=0,
                                            color='DarkSlateGrey'),
                                  color=np.array(c)[first_slider]),
                      selector=dict(mode='markers'), opacity=0.9)


    fig.show()

In [140]:
np.array(all_nouns)[first_lsa[:,0] > slider.value[0]]

array(['работа', 'система', 'состояние', 'качество', 'слово', 'элемент',
       'район', 'способность', 'результат', 'течение', 'год', 'путь',
       'рис', 'порт', 'основание', 'глина', 'угол', 'территория',
       'уровень', 'вода', 'ветер', 'рисунок', 'стадия', 'решение', 'этап',
       'область', 'земля', 'площадка', 'пункт', 'дорога', 'испытание',
       'возможность', 'рабочий', 'период', 'слой', 'мощность', 'место',
       'нагрузка', 'условие', 'масса', 'ход', 'ряд', 'недостаток', 'мочь',
       'глубина', 'объём', 'высота', 'лента', 'число', 'поле', 'состав',
       'поверхность', 'расход', 'ствол', 'запись', 'позиция', 'длина',
       'время', 'потеря', 'форма', 'образец', 'процесс', 'счёт', 'доля',
       'пространство', 'вид', 'стенка', 'сторона', 'зона', 'шаг', 'пояс',
       'цикл', 'скважина', 'начало', 'воздух', 'положение', 'энергия',
       'причина', 'раствор', 'предел', 'среда', 'газ', 'значение', 'мера',
       'железо', 'сеть', 'трещина', 'случай', 'канал', 'дейст

In [131]:
all_colors = {'anatomy': 'rgb(173, 255, 47)',
 'botanics': 'rgb(50, 205, 50)',
 'byology': 'rgb(152, 251, 152)',
 'chemistry': 'rgb(34, 139, 34)',
 'economics': 'rgb(255, 255, 0)',
 'finance': 'rgb(255, 215, 0)',
 'geology': 'rgb(0, 255, 127)',
 'hystory': 'rgb(250, 128, 114)',
 'law': 'rgb(255, 165, 0)',
 'linguistics': 'rgb(123, 104, 238)',
 'mathematics': 'rgb(123, 104, 238)',
 'medicine': 'rgb(154, 205, 50)',
 'military': 'rgb(255, 69, 0)',
 'physics': 'rgb(0, 206, 209)',
 'plants': 'rgb(0, 255, 127)',
 'religion': 'rgb(255, 69, 0)',
 'sport': 'rgb(119, 136, 153)',
 'technics': 'rgb(65, 105, 225)',
 'zoology': 'rgb(154, 205, 50)',
 'architecture': 'rgb(199, 21, 133)',
 'informatics': 'rgb(0, 0, 205)',
 'names': 'rgb(47, 79, 79)',
 'philology': 'rgb(0, 0, 205)',
 'philosophy': 'rgb(153, 50, 204)'}

In [156]:
all_data = get_dicts(dict_dir, dict_add_dir)
#all_colors = get_colors()
get_graph_3d(first_lsa, all_nouns)

In [163]:
get_graph_3d(first_lsa**3, all_nouns)